In [5]:
!pip install --upgrade pip

  Obtaining dependency information for pip from https://files.pythonhosted.org/packages/47/6a/453160888fab7c6a432a6e25f8afe6256d0d9f2cbd25971021da6491d899/pip-23.3.1-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 8.2 MB/s eta 0:00:009.0 MB/s eta 0:00:01
  Attempting uninstall: pip
    Found existing installation: pip 23.2.1
    Uninstalling pip-23.2.1:
      Successfully uninstalled pip-23.2.1


In [6]:
!pip install ultralytics

## Importing libraries

In [2]:
import cv2 as cv
from glob import glob
import os
import random
from ultralytics import YOLO
import os
import pandas as pd


## Installing numpy version 1.20.0 in order to tackle the error due to easyocr

In [76]:
!pip install numpy==1.20.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.4/15.4 MB 9.4 MB/s eta 0:00:000m eta 0:00:01:01:01
  Attempting uninstall: numpy
    Found existing installation: numpy 1.26.1
    Uninstalling numpy-1.26.1:
      Successfully uninstalled numpy-1.26.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
daal4py 2021.6.0 requires daal==2021.4.0, which is not installed.
lapx 0.5.5 requires numpy>=1.21.6, but you have numpy 1.20.0 which is incompatible.
tensorboard 2.11.2 requires protobuf<4,>=3.9.2, but you have protobuf 4.21.12 which is incompatible.
tensorflow 2.11.0 requires protobuf<3.20,>=3.9.2, but you have protobuf 4.21.12 which is incompatible.
ultralytics 8.0.206 requires numpy>=1.22.2, but you have numpy 1.20.0 which is incompatible.


In [3]:
import numpy
import numpy.typing as npt
import easyocr


In [65]:
!pip install easyocr

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 2.5 MB/s eta 0:00:002.5 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.2/307.2 kB 3.4 MB/s eta 0:00:00 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.1/49.1 MB 10.5 MB/s eta 0:00:00m eta 0:00:010:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 674.2/674.2 kB 11.5 MB/s eta 0:00:0031m15.4 MB/s eta 0:00:01


In [4]:
videos = glob('highway_video.mp4')
print(videos)
print(type(videos))

['highway_video.mp4']
<class 'list'>


In [5]:
car_detector_model = YOLO('./models/yolov8n.pt')

In [43]:
print(type(car_detector_model))

<class 'ultralytics.models.yolo.model.YOLO'>


In [13]:
video = cv.VideoCapture(videos[0])

In [14]:
print(type(video))

<class 'cv2.VideoCapture'>


In [15]:
frame_width = int(video.get(3))
frame_height = int(video.get(4))
size = (frame_width, frame_height)

In [16]:
print(frame_width)
print(frame_height)
print(size)

3840
2160
(3840, 2160)


In [6]:
numberplate_detector_model = YOLO("../numberPlateDetctionModel/model/epoch1.pt")

In [18]:
result = numberplate_detector_model('./car_image.jpg')


image 1/1 /home/bhushan/Documents/DSAI/Projects/Number-Plate-Detection-Project/pipeline/car_image.jpg: 448x640 1 licenseplate, 84.6ms
Speed: 2.3ms preprocess, 84.6ms inference, 0.9ms postprocess per image at shape (1, 3, 448, 640)


In [19]:
print(result[0].boxes.data.tolist())

[[129.56878662109375, 302.95440673828125, 189.2602996826172, 325.9913635253906, 0.2857583463191986, 0.0]]


## Step 1 Implementing the car detection

In [47]:
video = cv.VideoCapture(videos[0])

ret = True
frame_number = -1
# all vehicle class IDs from the COCO dataset (car, motorbike, truck) https://docs.ultralytics.com/datasets/detect/coco/#dataset-yaml
vehicles = [2,3,5]
vehicle_bounding_boxes = []

# read the 10 first frames
while ret:
    frame_number += 1
    ret, frame = video.read()

    if ret and frame_number < 10:
        # use track() to identify instances and track them frame by frame
        detections = car_detector_model.track(frame, persist=True)[0]
        # save cropped detections
        # detections.save_crop('outputs')
        # print nodel predictions for debugging
        # print(results)

        for detection in detections.boxes.data.tolist():
            # print detection bounding boxes for debugging
            # print(detection)
            x1, y1, x2, y2, track_id, score, class_id = detection
            # I am only interested in class IDs that belong to vehicles
            if int(class_id) in vehicles and score > 0.5:
                vehicle_bounding_boxes.append([x1, y1, x2, y2, track_id, score])

# print found bounding boxes for debugging
print(vehicle_bounding_boxes)
video.release()


0: 384x640 10 cars, 47.4ms
Speed: 3.6ms preprocess, 47.4ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 10 cars, 1 truck, 67.3ms
Speed: 3.1ms preprocess, 67.3ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 10 cars, 60.3ms
Speed: 4.1ms preprocess, 60.3ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 cars, 1 truck, 57.5ms
Speed: 2.6ms preprocess, 57.5ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 cars, 1 truck, 62.4ms
Speed: 2.9ms preprocess, 62.4ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 cars, 1 truck, 61.5ms
Speed: 2.3ms preprocess, 61.5ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 cars, 1 truck, 67.2ms
Speed: 3.2ms preprocess, 67.2ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 9 cars, 1 truck, 64.0ms
Speed: 3.5ms preprocess, 64.0ms inference, 0.9ms

[[2043.254638671875, 878.530029296875, 2427.3505859375, 1226.425048828125, 1.0, 0.8946591019630432], [3.304290771484375, 687.6639404296875, 354.3390197753906, 985.408447265625, 2.0, 0.8668078184127808], [752.2139892578125, 1369.3121337890625, 1429.3065185546875, 1984.0484619140625, 3.0, 0.8637262582778931], [1150.0830078125, 1302.9462890625, 1644.849365234375, 1800.72802734375, 4.0, 0.8433957099914551], [2195.68017578125, 1157.04931640625, 2786.025390625, 1736.6319580078125, 5.0, 0.8106945753097534], [1246.8182373046875, 1009.6560668945312, 1745.5445556640625, 1426.886474609375, 6.0, 0.7685909867286682], [477.69598388671875, 1961.5523681640625, 1173.67529296875, 2151.64697265625, 7.0, 0.6864073872566223], [1293.87744140625, 840.595703125, 1677.9261474609375, 1062.569580078125, 8.0, 0.6573163270950317], [596.8541259765625, 583.9827270507812, 807.2604370117188, 774.1543579101562, 9.0, 0.609666645526886], [2236.02294921875, 809.560546875, 2553.464111328125, 1055.5653076171875, 10.0, 0.608

## STEP 2 Implementing the License Plate Detection

In [48]:
# read video by index
video = cv.VideoCapture(videos[0])

ret = True
frame_number = -1
vehicles = [2,3,5]

# read the 10 first frames
while ret:
    frame_number += 1
    ret, frame = video.read()

    if ret and frame_number < 10:
        
        # vehicle detector
        detections = car_detector_model.track(frame, persist=True)[0]
        for detection in detections.boxes.data.tolist():
            x1, y1, x2, y2, track_id, score, class_id = detection
            if int(class_id) in vehicles and score > 0.5:
                vehicle_bounding_boxes = []
                vehicle_bounding_boxes.append([x1, y1, x2, y2, track_id, score])
                for bbox in vehicle_bounding_boxes:
                    print(bbox)
                    roi = frame[int(y1):int(y2), int(x1):int(x2)]
                    # debugging check if bbox lines up with detected vehicles (should be identical to save_crops() above
                    # cv.imwrite(str(track_id) + '.jpg', roi)
                    
                    # license plate detector for region of interest
                    license_plates = numberplate_detector_model(roi)[0]
                    # check every bounding box for a license plate
                    for license_plate in license_plates.boxes.data.tolist():
                        plate_x1, plate_y1, plate_x2, plate_y2, plate_score, _ = license_plate
                        # verify detections
                        print(license_plate, 'track_id: ' + str(bbox[4]))
                        plate = roi[int(plate_y1):int(plate_y2), int(plate_x1):int(plate_x2)]
                        cv.imwrite(str(track_id) + '.jpg', plate)
                        
video.release()


0: 384x640 10 cars, 68.9ms
Speed: 3.2ms preprocess, 68.9ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 608x640 (no detections), 78.2ms
Speed: 2.8ms preprocess, 78.2ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)

0: 544x640 (no detections), 73.6ms
Speed: 2.8ms preprocess, 73.6ms inference, 0.4ms postprocess per image at shape (1, 3, 544, 640)



[2043.254638671875, 878.530029296875, 2427.3505859375, 1226.425048828125, 1.0, 0.8946591019630432]
[3.304290771484375, 687.6639404296875, 354.3390197753906, 985.408447265625, 2.0, 0.8668078184127808]
[752.2139892578125, 1369.3121337890625, 1429.3065185546875, 1984.0484619140625, 3.0, 0.8637262582778931]


0: 608x640 (no detections), 72.5ms
Speed: 3.6ms preprocess, 72.5ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)

0: 640x640 (no detections), 79.1ms
Speed: 3.5ms preprocess, 79.1ms inference, 0.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 65.9ms
Speed: 2.7ms preprocess, 65.9ms inference, 0.5ms postprocess per image at shape (1, 3, 640, 640)



[1150.0830078125, 1302.9462890625, 1644.849365234375, 1800.72802734375, 4.0, 0.8433957099914551]
[2195.68017578125, 1157.04931640625, 2786.025390625, 1736.6319580078125, 5.0, 0.8106945753097534]
[1246.8182373046875, 1009.6560668945312, 1745.5445556640625, 1426.886474609375, 6.0, 0.7685909867286682]


0: 544x640 1 licenseplate, 71.7ms
Speed: 2.5ms preprocess, 71.7ms inference, 1.1ms postprocess per image at shape (1, 3, 544, 640)

0: 192x640 (no detections), 36.2ms
Speed: 0.9ms preprocess, 36.2ms inference, 0.4ms postprocess per image at shape (1, 3, 192, 640)

0: 384x640 (no detections), 62.6ms
Speed: 1.8ms preprocess, 62.6ms inference, 0.5ms postprocess per image at shape (1, 3, 384, 640)

0: 608x640 (no detections), 76.9ms
Speed: 2.4ms preprocess, 76.9ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)



...

[708.4771728515625, 1419.32861328125, 1414.89794921875, 2065.75732421875, 1.0, 0.8703704476356506]
[1117.118408203125, 1355.48046875, 1632.835693359375, 1859.1971435546875, 2.0, 0.8578417301177979]
[2036.3243408203125, 892.3719482421875, 2431.3759765625, 1242.56103515625, 3.0, 0.8542649745941162]


0: 576x640 (no detections), 61.7ms
Speed: 2.4ms preprocess, 61.7ms inference, 0.6ms postprocess per image at shape (1, 3, 576, 640)

0: 544x640 (no detections), 56.1ms
Speed: 2.5ms preprocess, 56.1ms inference, 0.4ms postprocess per image at shape (1, 3, 544, 640)

0: 608x640 (no detections), 60.9ms
Speed: 2.7ms preprocess, 60.9ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)

0: 384x640 (no detections), 43.8ms
Speed: 1.9ms preprocess, 43.8ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)



[1232.0665283203125, 1038.4925537109375, 1737.7298583984375, 1457.2987060546875, 4.0, 0.848140299320221]
[2196.344970703125, 1195.93212890625, 2828.767822265625, 1793.272705078125, 5.0, 0.7637737393379211]
[1298.177490234375, 855.585205078125, 1682.0235595703125, 1077.0677490234375, 6.0, 0.7355586290359497]
[43.3426513671875, 679.41650390625, 403.8916931152344, 962.6008911132812, 7.0, 0.73131263256073]


0: 512x640 (no detections), 55.8ms
Speed: 2.4ms preprocess, 55.8ms inference, 0.4ms postprocess per image at shape (1, 3, 512, 640)

0: 608x640 (no detections), 81.1ms
Speed: 2.5ms preprocess, 81.1ms inference, 0.4ms postprocess per image at shape (1, 3, 608, 640)

0: 576x640 (no detections), 57.6ms
Speed: 2.2ms preprocess, 57.6ms inference, 0.5ms postprocess per image at shape (1, 3, 576, 640)


[621.3924560546875, 583.3522338867188, 824.3472290039062, 772.8421020507812, 8.0, 0.6403359174728394]
[2127.16162109375, 452.0165100097656, 2425.124755859375, 709.0887451171875, 10.0, 0.6066041588783264]


## STEP 3 Preprocess License Plates

In [49]:
# read video by index
video = cv.VideoCapture(videos[0])

ret = True
frame_number = -1
vehicles = [2,3,5]

# read the 10 first frames
while ret:
    frame_number += 1
    ret, frame = video.read()

    if ret and frame_number < 100:
        
        # vehicle detector
        detections = car_detector_model.track(frame, persist=True)[0]
        for detection in detections.boxes.data.tolist():
            x1, y1, x2, y2, track_id, score, class_id = detection
            if int(class_id) in vehicles and score > 0.5:
                vehicle_bounding_boxes = []
                vehicle_bounding_boxes.append([x1, y1, x2, y2, track_id, score])
                for bbox in vehicle_bounding_boxes:
                    print(bbox)
                    roi = frame[int(y1):int(y2), int(x1):int(x2)]
                    
                    # license plate detector for region of interest
                    license_plates = numberplate_detector_model(roi)[0]
                    # process license plate
                    for license_plate in license_plates.boxes.data.tolist():
                        plate_x1, plate_y1, plate_x2, plate_y2, plate_score, _ = license_plate
                        # crop plate from region of interest
                        plate = roi[int(plate_y1):int(plate_y2), int(plate_x1):int(plate_x2)]
                        # de-colorize
                        plate_gray = cv.cvtColor(plate, cv.COLOR_BGR2GRAY)
                        # posterize
                        _, plate_treshold = cv.threshold(plate_gray, 64, 255, cv.THRESH_BINARY_INV)
                        cv.imwrite(str(track_id) + '_gray.jpg', plate_gray)
                        cv.imwrite(str(track_id) + '_thresh.jpg', plate_treshold)
                        
video.release()


0: 384x640 10 cars, 79.5ms
Speed: 4.1ms preprocess, 79.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 608x640 (no detections), 77.4ms
Speed: 2.6ms preprocess, 77.4ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)

0: 544x640 (no detections), 85.0ms
Speed: 2.4ms preprocess, 85.0ms inference, 0.5ms postprocess per image at shape (1, 3, 544, 640)



[2043.254638671875, 878.530029296875, 2427.3505859375, 1226.425048828125, 1.0, 0.8946591019630432]
[3.304290771484375, 687.6639404296875, 354.3390197753906, 985.408447265625, 2.0, 0.8668078184127808]
[752.2139892578125, 1369.3121337890625, 1429.3065185546875, 1984.0484619140625, 3.0, 0.8637262582778931]


0: 608x640 (no detections), 74.0ms
Speed: 3.2ms preprocess, 74.0ms inference, 0.4ms postprocess per image at shape (1, 3, 608, 640)

0: 640x640 (no detections), 82.2ms
Speed: 3.2ms preprocess, 82.2ms inference, 0.5ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 92.8ms
Speed: 3.4ms preprocess, 92.8ms inference, 0.4ms postprocess per image at shape (1, 3, 640, 640)



[1150.0830078125, 1302.9462890625, 1644.849365234375, 1800.72802734375, 4.0, 0.8433957099914551]
[2195.68017578125, 1157.04931640625, 2786.025390625, 1736.6319580078125, 5.0, 0.8106945753097534]
[1246.8182373046875, 1009.6560668945312, 1745.5445556640625, 1426.886474609375, 6.0, 0.7685909867286682]


0: 544x640 1 licenseplate, 62.7ms
Speed: 2.9ms preprocess, 62.7ms inference, 0.7ms postprocess per image at shape (1, 3, 544, 640)

0: 192x640 (no detections), 32.0ms
Speed: 0.9ms preprocess, 32.0ms inference, 0.4ms postprocess per image at shape (1, 3, 192, 640)

0: 384x640 (no detections), 48.4ms
Speed: 1.5ms preprocess, 48.4ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 608x640 (no detections), 82.9ms
Speed: 2.6ms preprocess, 82.9ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)



...

[1177.8599853515625, 1028.962890625, 1631.0965576171875, 1423.3284912109375, 4.0, 0.8260940909385681]
[0.0, 697.7089233398438, 269.3365173339844, 966.1268920898438, 5.0, 0.7989657521247864]


0: 640x640 (no detections), 118.3ms
Speed: 3.5ms preprocess, 118.3ms inference, 0.8ms postprocess per image at shape (1, 3, 640, 640)

0: 288x640 (no detections), 59.2ms
Speed: 2.2ms preprocess, 59.2ms inference, 0.6ms postprocess per image at shape (1, 3, 288, 640)

0: 544x640 (no detections), 73.2ms
Speed: 3.2ms preprocess, 73.2ms inference, 0.6ms postprocess per image at shape (1, 3, 544, 640)



[2316.06005859375, 1760.874267578125, 3271.343505859375, 2148.23388671875, 6.0, 0.7917913198471069]
[437.7599182128906, 589.26025390625, 718.7716064453125, 819.6832885742188, 7.0, 0.7403950691223145]
[2251.8291015625, 953.8873291015625, 2657.710693359375, 1311.44140625, 8.0, 0.6707457304000854]


0: 576x640 (no detections), 81.5ms
Speed: 3.8ms preprocess, 81.5ms inference, 0.6ms postprocess per image at shape (1, 3, 576, 640)

0: 640x640 (no detections), 79.8ms
Speed: 3.1ms preprocess, 79.8ms inference, 0.6ms postprocess per image at shape (1, 3, 640, 640)


[1338.706787109375, 903.0655517578125, 1724.652099609375, 1285.8116455078125, 9.0, 0.636570930480957]


## Pipeline

In [7]:
# Initialize the OCR reader
reader = easyocr.Reader(['en'], gpu=True)

Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


In [8]:
# Mapping dictionaries for character conversion
# characters that can easily be confused can be 
# verified by their location - an `O` in a place
# where a number is expected is probably a `0`
dict_char_to_int = {'O': '0',
                    'I': '1',
                    'J': '3',
                    'A': '4',
                    'G': '6',
                    'S': '5'}

dict_int_to_char = {'0': 'O',
                    '1': 'I',
                    '3': 'J',
                    '4': 'A',
                    '6': 'G',
                    '5': 'S'}

In [9]:
def license_complies_format(text):
    # True if the license plate complies with the format, False otherwise.
    if len(text) != 7:
        return False

    if (text[0] in string.ascii_uppercase or text[0] in dict_int_to_char.keys()) and \
       (text[1] in string.ascii_uppercase or text[1] in dict_int_to_char.keys()) and \
       (text[2] in ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9'] or text[2] in dict_char_to_int.keys()) and \
       (text[3] in ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9'] or text[3] in dict_char_to_int.keys()) and \
       (text[4] in string.ascii_uppercase or text[4] in dict_int_to_char.keys()) and \
       (text[5] in string.ascii_uppercase or text[5] in dict_int_to_char.keys()) and \
       (text[6] in string.ascii_uppercase or text[6] in dict_int_to_char.keys()):
        return True
    else:
        return False

In [10]:
def format_license(text):
    license_plate_ = ''
    mapping = {0: dict_int_to_char, 1: dict_int_to_char, 4: dict_int_to_char, 5: dict_int_to_char, 6: dict_int_to_char,
               2: dict_char_to_int, 3: dict_char_to_int}
    for j in [0, 1, 2, 3, 4, 5, 6]:
        if text[j] in mapping[j].keys():
            license_plate_ += mapping[j][text[j]]
        else:
            license_plate_ += text[j]

    return license_plate_

In [11]:
def read_license_plate_robust(license_plate_crop):
    detections = reader.readtext(license_plate_crop)

    for detection in detections:
        bbox, text, score = detection

        text = text.upper().replace(' ', '')

        # verify that text is conform to a standard license plate
        if license_complies_format(text):
            # bring text into the default license plate format
            return format_license(text), score

    return None, None

In [12]:
def read_license_plate(license_plate_crop):
    detections = reader.readtext(license_plate_crop)

    for detection in detections:
        bbox, text, score = detection

        text = text.upper().replace(' ', '')
        
        return text, score

    return None, None

In [23]:
results_webcam = pd.DataFrame(columns=['frame_no', 'track_id', 'car_x1', 'car_y1', 'car_x2', 'car_y2', 'car_score', 'plate_x1', 'plate_y1', 'plate_x2', 'plate_y2', 'plate_score', 'plate_no', 'plateno_score'])

# read video by index
video = cv.VideoCapture(videos[0])

ret = True
frame_number = -1
vehicles = [2,3,5]

# read the entire video
while ret:
    ret, frame = video.read()
    frame_number += 1
#     cv.imshow("Webcam", frame)
    if ret:      
        # vehicle detector
        detections = car_detector_model.track(frame, persist=True)[0]
        for detection in detections.boxes.data.tolist():
            x1, y1, x2, y2, track_id, score, class_id = detection
            if int(class_id) in vehicles and score > 0.5:
                vehicle_bounding_boxes = []
                vehicle_bounding_boxes.append([x1, y1, x2, y2, track_id, score])
                for bbox in vehicle_bounding_boxes:
                    print(bbox)
                    roi = frame[int(y1):int(y2), int(x1):int(x2)]
                    
                    # license plate detector for region of interest
                    license_plates = numberplate_detector_model(roi)[0]
                    # process license plate
                    for license_plate in license_plates.boxes.data.tolist():
                        plate_x1, plate_y1, plate_x2, plate_y2, plate_score, _ = license_plate
                        # crop plate from region of interest
                        plate = roi[int(plate_y1):int(plate_y2), int(plate_x1):int(plate_x2)]
                        # de-colorize
                        plate_gray = cv.cvtColor(plate, cv.COLOR_BGR2GRAY)
                        # posterize
                        _, plate_treshold = cv.threshold(plate_gray, 64, 255, cv.THRESH_BINARY_INV)
                        
                        # OCR
                        np_text, np_score = read_license_plate(plate_treshold)
                        # if plate could be read write results
                        if np_text is not None:
                            r = {'frame_no': frame_number, 'track_id': track_id, 'car_x1': x1, 'car_y1':y1, 'car_x2':x2, 'car_y2':y2, 'car_score':score, 'plate_x1':plate_x1, 'plate_y1':plate_y1, 'plate_x2':plate_x2, 'plate_y2':plate_y2, 'plate_score':plate_score, 'plate_no':np_text, 'plateno_score':np_score}
                            results_webcam = pd.concat([results_webcam, pd.DataFrame([r])], ignore_index=True)
results_webcam.to_csv('results_webcam.csv', index=False)
video.release()


0: 384x640 10 cars, 78.3ms
Speed: 3.3ms preprocess, 78.3ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 608x640 (no detections), 82.6ms
Speed: 3.1ms preprocess, 82.6ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)

0: 544x640 (no detections), 67.8ms
Speed: 3.0ms preprocess, 67.8ms inference, 0.5ms postprocess per image at shape (1, 3, 544, 640)



[2043.254638671875, 878.530029296875, 2427.3505859375, 1226.425048828125, 1.0, 0.8946591019630432]
[3.304290771484375, 687.6639404296875, 354.3390197753906, 985.408447265625, 2.0, 0.8668078184127808]
[752.2139892578125, 1369.3121337890625, 1429.3065185546875, 1984.0484619140625, 3.0, 0.8637262582778931]


0: 608x640 (no detections), 86.7ms
Speed: 3.7ms preprocess, 86.7ms inference, 0.5ms postprocess per image at shape (1, 3, 608, 640)

0: 640x640 (no detections), 87.0ms
Speed: 3.8ms preprocess, 87.0ms inference, 0.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 (no detections), 78.5ms
Speed: 3.8ms preprocess, 78.5ms inference, 0.5ms postprocess per image at shape (1, 3, 640, 640)



[1150.0830078125, 1302.9462890625, 1644.849365234375, 1800.72802734375, 4.0, 0.8433957099914551]
[2195.68017578125, 1157.04931640625, 2786.025390625, 1736.6319580078125, 5.0, 0.8106945753097534]
[1246.8182373046875, 1009.6560668945312, 1745.5445556640625, 1426.886474609375, 6.0, 0.7685909867286682]


0: 544x640 1 licenseplate, 82.3ms
Speed: 2.6ms preprocess, 82.3ms inference, 0.8ms postprocess per image at shape (1, 3, 544, 640)

0: 192x640 (no detections), 48.0ms
Speed: 0.9ms preprocess, 48.0ms inference, 0.4ms postprocess per image at shape (1, 3, 192, 640)

0: 384x640 (no detections), 69.9ms
Speed: 1.6ms preprocess, 69.9ms inference, 0.5ms postprocess per image at shape (1, 3, 384, 640)



...

0: 640x640 (no detections), 107.0ms
Speed: 3.1ms preprocess, 107.0ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)

0: 224x640 (no detections), 46.4ms
Speed: 2.3ms preprocess, 46.4ms inference, 0.6ms postprocess per image at shape (1, 3, 224, 640)

0: 608x640 (no detections), 117.4ms
Speed: 3.7ms preprocess, 117.4ms inference, 0.7ms postprocess per image at shape (1, 3, 608, 640)



[498.47607421875, 1891.7646484375, 1281.4888916015625, 2153.0302734375, 6.0, 0.7591179609298706]
[1057.518798828125, 1252.235107421875, 1593.544677734375, 1735.6461181640625, 7.0, 0.7535707354545593]
[1409.6876220703125, 776.2279052734375, 1753.8988037109375, 1086.208984375, 8.0, 0.7342813611030579]


0: 608x640 (no detections), 113.1ms
Speed: 3.2ms preprocess, 113.1ms inference, 0.7ms postprocess per image at shape (1, 3, 608, 640)

0: 480x640 (no detections), 95.2ms
Speed: 3.5ms preprocess, 95.2ms inference, 0.7ms postprocess per image at shape (1, 3, 480, 640)

0: 640x160 (no detections), 61.5ms
Speed: 1.2ms preprocess, 61.5ms inference, 0.6ms postprocess per image at shape (1, 3, 640, 160)



[792.7196655273438, 1404.54931640625, 1429.5791015625, 1874.3291015625, 9.0, 0.7235838770866394]
[0.017131805419921875, 706.2376708984375, 79.86125183105469, 1091.867431640625, 11.0, 0.6516286730766296]
[2109.197021484375, 785.934814453125, 2557.693603515625, 1220.9381103515625, 12.0, 0.6384185552597046]


0: 640x640 (no detections), 121.6ms
Speed: 3.5ms preprocess, 121.6ms inference, 0.7ms postprocess per image at shape (1, 3, 640, 640)


In [22]:
results_webcam.head()

Empty DataFrame
Columns: [frame_no, track_id, car_x1, car_y1, car_x2, car_y2, car_score, plate_x1, plate_y1, plate_x2, plate_y2, plate_score, plate_no, plateno_score]
Index: []

In [20]:
videos

['highway_video.mp4']